# Source code to retrieve data and plot

In [4]:
import os, glob
import numpy as np
import networkx as nx
import itertools as it, matplotlib.pyplot as mb
mb.rcParams['text.usetex'] = True
import pandas as pd

In [7]:
def fixonecomp(fp,f,N):  #fixation probability for the complete graph under dB updating
    phi=0
    if(fp != f):
        phi=((N-1)/N)*(1-(f/fp))/(1-(f/fp)**(N-1))  
    else:
        phi=1/N    
    return phi;


def weight_mat_dB(adjmat):            # function that converts an adjacency matrix of 0's and 1's to its corresponding weight matrix.
    weighmat=np.zeros(np.shape(adjmat))
    for i in range(np.shape(adjmat)[0]):
        for j in range(np.shape(adjmat)[1]):
            if(np.sum(adjmat[:,j])!= 0):
                weighmat[i,j]=adjmat[i,j]/(np.sum(adjmat[:,j]))
            else:
                weighmat[i,j]=0
    return weighmat;

In [8]:
path=os.getcwd()
subpath='/Data/Fig_3/dB/'    # Path to the directory where data is saved.


In [9]:
files=[]
for f in os.listdir(path+subpath):
        if f.endswith('.npy'):
            files.append(f)

In [17]:
link_prob=[]
seed_no=[]
for row in files:
    arglist = row.split('_')
    link_prob.append(float(arglist[arglist.index('p')+1]))
    seed_no.append(int(arglist[arglist.index('no')+1].split('.')[0]))
    
link_prob=sorted(np.unique(link_prob))  
seed_no=sorted(np.unique(seed_no))
N=np.shape(np.load(path+subpath+row)[0])[0]

In the cell below, uncomment the line if you want to generate the figure for temperature initialsied dB updating and comment the last line of the cell.

In [12]:
r=[0.5,0.75,1,1.25,1.5,1.75,2.0,2.25,2.5]
Fix_prob=np.zeros((np.size(link_prob),np.size(seed_no),np.size(r)))
for row in files: 
    arglist = row.split('_')
    p=float(arglist[arglist.index('p')+1])
    seed=int(arglist[arglist.index('no')+1].split('.')[0])
    G=nx.erdos_renyi_graph(N, p, seed, directed=False)
    A=nx.to_numpy_matrix(G,dtype=int)
    if(nx.is_connected(G)==True):
        for i in range(np.size(r)):
            fix_prob_nodes=np.load(path+subpath+row)[i][:,1]
            #Fix_prob[link_prob.index(p),seed_no.index(seed),i]=np.average(fix_prob_nodes,weights=np.sum(weight_mat_dB(A),axis=1))
            Fix_prob[link_prob.index(p),seed_no.index(seed),i]=np.average(fix_prob_nodes,weights=None)
        
       

In [13]:
fix_comp=np.zeros(np.size(r))
for i in range(np.size(r)):
    fix_comp[i]=fixonecomp(r[i],1,N)


In [14]:
Amplifier_fix=[]
Supp_fix=[]
Amplifier=[]
Supp_sel=[]
Complete=[]
Unconnected=[]
Unclassified=[]
for i in range(np.size(link_prob)):
    for j in range(np.size(seed_no)):
        p=link_prob[i]
        G=nx.erdos_renyi_graph(N, p, j, directed=False)
        A=nx.to_numpy_matrix(G,dtype=int)
        if(nx.is_connected(G)==False):
            Unconnected.append(link_prob[i])
        elif((A==nx.to_numpy_matrix(nx.complete_graph(N),dtype=int)).all()):
            Complete.append(link_prob[i])
        elif(np.all(np.less(Fix_prob[link_prob.index(p),seed_no.index(j),0:2],fix_comp[0:2]))==True and np.all(np.greater(Fix_prob[link_prob.index(p),seed_no.index(j),3:],fix_comp[3:]))==True):
            Amplifier.append(link_prob[i])
        elif((np.all(np.greater(Fix_prob[link_prob.index(p),seed_no.index(j),0:3],fix_comp[0:3]))==True and np.all(np.less(Fix_prob[link_prob.index(p),seed_no.index(j),3:],fix_comp[3:]))==True and np.greater(Fix_prob[link_prob.index(p),seed_no.index(j),2]-fix_comp[2],0.001)==True) or (np.all(np.greater(Fix_prob[link_prob.index(p),seed_no.index(j),0:4],fix_comp[0:4]))==True)):
            Amplifier_fix.append(link_prob[i])    
        elif(np.all(np.greater(Fix_prob[link_prob.index(p),seed_no.index(j),0:2],fix_comp[0:2]))==True and np.all(np.less(Fix_prob[link_prob.index(p),seed_no.index(j),3:],fix_comp[3:]))==True):
            Supp_sel.append(link_prob[i])
        elif(np.all(np.less(Fix_prob[link_prob.index(p),seed_no.index(j),0:2],fix_comp[0:2]))==True and np.all(np.less(Fix_prob[link_prob.index(p),seed_no.index(j),3:],fix_comp[3:]))==True):
            Supp_fix.append(link_prob[i])
        else:
            Unclassified.append(link_prob[i])
            
for j in range(500):
    Complete.append(1.0)


In [15]:
df0=pd.DataFrame( Unconnected,columns=['Disconnected'])
df1=pd.DataFrame( Amplifier,columns=['AoS'])
df2=pd.DataFrame( Supp_sel,columns=['SoS'])
df3=pd.DataFrame( Amplifier_fix,columns=[' Piecewise AoF'])
df4=pd.DataFrame( Supp_fix,columns=['SoF'])
df5=pd.DataFrame( Complete,columns=['Complete'])
df6=pd.DataFrame( Unclassified,columns=['Unclassified'])
df=pd.concat([df0,df6,df1,df2,df3,df4,df5], ignore_index=True)

In [18]:
%matplotlib widget
df.plot.hist(stacked=True, bins=np.size(link_prob)+1, figsize=(10, 6),color=['white','yellow', 'green','red','orange','#ff80ff','blue'],alpha=1,edgecolor='black', linewidth=0.8)
mb.xlabel("Probability of link connection", fontsize=17)
mb.ylabel("Number of graphs", fontsize=17)
mb.legend(loc='lower left', fontsize=18)
mb.xticks(fontsize=26)
mb.yticks(fontsize=26)

mb.show()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …